# Instructions
The following code was designed in order to calculate the number of cells within an image or set of images.

### A few pertinent features of the code:
This code calculates the number of counted cells on up to two channels, as well as overlapping cells across channels.
In addition to cell count, the locations of counted cells can be saved.
Lastly, a region of interest based upon a user-made mask can be specified and cell counting can be restricted to this region of interest.  The size of the region of interest in pixels is returned. 

### Folder Structure

For this code to work files should be organized in a specific manner.
Directory_Main (the path of which is to be defined by the user... actual directory name can be whatever you want) should contain the subfolders "Ch1","Ch2",and "ROI" (these names matter).
If you are not using ROIs, this folder can be excluded.
Similarly, if only one channel is being examined, Ch1/Ch2 can be exluded.
Ch1 and Ch2 folders should contain 8-bit .tif images with files of the same name, though some suffix identifying the channel (e.g. "_Ch1") is fine.  This is required in order for images for each channel of a multichannel image to be matched.
ROI should contain .tif images with ROI masks, described below.  These should be named similarly to files in Ch1 and Ch2.
Example filenames under Ch1, Ch2, and ROI: "Mouse1_Image1_Ch1.tif","Mouse1_Image1_Ch2.tif",""Mouse1_Image1_ROI.tif"

### Making ROIs
Regions of interest are best drawn using ImajeJ.  Binary masks are created such that the region of interest pixel values = 255, whereas other values are equal to 0
#1 - Open the image in ImageJ
#2 - Use your preferred selection tool (I like freehand selection tool) to outline the region of interest
#3 - Go to edit > selection > create mask
#4 - Save the mask as .tif file

### Requirements
See README for dependencies and conda environment install instructions

### What type of cells can this count?
Any semi-circular cell that is more or less filled by the fluorescent label will be cable of being counted.  If the cells are only visible by their perimeter than this code as is may not work. In this case, a process should be applied to either a) fill the internal component of the cell after thresholding or b) use smoothing or morphological opening to increase the internal of the cell. Although watershed can separate cells to some extent, a large degree ov overlap is unable to be overcome.

## Setting parameters:
All parameters required to be set by the user is set in the first cell of code.  
1 - Cell Diameter:  This is the average cell diameter in pixel units.  Can be obtained easily with ImageJ measurement tool.
2 - Threshold:  This is to be obtained using the optimization procedure or by setting by eye (not advised).
3 - Paricle Minimum: After thresholding this serves to erase excessively small points.  Proportion of average cell size permitted.  Average cell size is assumed to be square of diamater for rough approximation
4 - Use ROI:  Are you using an ROI or analyzing the entire image?
5- Use Watershed: Watershed procedure attempts to separate adjoining cells. 


# 1. Load Necessary Packages

In [15]:
%load_ext autoreload
%autoreload 2
import pylab 
import os
import fnmatch
import imread
import cv2
import numpy as np
import mahotas as mh 
import pandas as pd
import holoviews as hv
import CellCounter_Functions as cc

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# 2. User Specifies Parameters and Options for Running
***Windows Users:*** Place an 'r' in front directory path (e.g. r"zp\Videos") to avoid mishandling of forward slashes.

In [16]:
#Define directory of working environment (Directory.Main)
dirinfo = {
    'main' : "/Users/zachpennington/Documents/ZachsDocuments/Sinai.PostDoc/Projects/SEFL/SEFL_2/MEA_Images/Counts/"
}

#Set Parameters
params = {
    'ch1_diam' : 10 ,#Average Cell Diameter in pixel units.  Must be integer value.  
    'ch1_thresh' : 36 ,#Set threshold to integer value based upon CellCounter_Optimization.ipynb
    'ch2_diam' : 5 ,#Average Cell Diameter in pixel units.  Must be integer value.  
    'ch2_thresh' : 5 ,#Set threshold to integer value based upon CellCounter_Optimization.ipynb
    'particle_min' : 0.2 ,#After thresholding this serves to erase excessively small points.  Proportion of average cell size permitted.  Average cell size is assumed to be square of diamater for rough approximation.  0.2 has worked well for me
    'overlap' : .5 #When measuring overlap of two channels, this is the minimum amount of overlap permitted, as a proportion of average cell size for channel with smaller diameter cells.  Average cell size is assumed to be square of diamater for rough approximation.
}

dirinfo = cc.getdirinfo(dirinfo)


# 3. Display Example Process for One Channel (Optional)
The code helps display the processing results for a single image.  The original image, the background subtracted and smoothed image, the thresholded image, and the final cell locations are displayed.   By default displays results from first image of first channel.  Primarily used for troubleshooting.  Can't view ROI this way

Set channel equal to "Ch1" or "Ch2".  Additionally, file number can be set based upon alphabetical ordering of files (0 is first file, etc)

To toggle whether an ROI or Watershed are to be used, set to True or False

In [19]:
%%output size=100

#Specify Image to Look at Below
Channel = "Ch1" #Specify Ch1 or Ch2
file = 15 #Specify index in folder.  0 by default

#call function to count cells
count_out = cc.Count(file,Channel,params,dirinfo,
                     UseROI=True,
                     UseWatershed=True)
display = cc.display_count(count_out)
display.cols(2)

Processing: MEA_M14_4-Image Export-16_c1_ORG.tif
Cells: 28


:Layout
   .Image.I   :Image   [x,y]   (z)
   .Image.II  :Image   [x,y]   (z)
   .Image.III :Image   [x,y]   (z)
   .Image.IV  :Image   [x,y]   (z)

# 4. Display Example Process of Overlap 
The code helps display the overlap results for a single set of images (where each image is a different channel).  The original images, the final cell locations, and the overlapping cells are displayed.

In [ ]:
%%output size=100
#Specify Image to Look at Below
file = 0 #Specify index in folder.  0 by default


#call function to count cells
count_out1 = cc.Count(file,"Ch1",params,dirinfo,
                     UseROI=False,
                     UseWatershed=True)
count_out2 = cc.Count(file,"Ch2",params,dirinfo,
                     UseROI=False,
                     UseWatershed=True)
merge_out = cc.Merge(count_out1['cells'],count_out2['cells'],params)
display = cc.display_merge(count_out1,count_out2,merge_out)
display.cols(2)


# 5. Count Channel 1
Count all cells for channel 1 images and save to disk

In [20]:
Ch1_Counts = cc.Count_folder(dirinfo,params,
                             Channel="Ch1",
                             UseROI=True,
                             UseWatershed=True)
Ch1_Counts.to_csv(os.path.join(os.path.normpath(dirinfo['output']), "Ch1_Counts.csv"))
Ch1_Counts

Processing: MEA_M10_1-Image Export-01_c1_ORG.tif
Cells: 29
Processing: MEA_M10_2-Image Export-02_c1_ORG.tif
Cells: 43
Processing: MEA_M10_3-Image Export-03_c1_ORG.tif
Cells: 0
Processing: MEA_M10_4-Image Export-04_c1_ORG.tif
Cells: 5
Processing: MEA_M12_1-Image Export-05_c1_ORG.tif
Cells: 35
Processing: MEA_M12_2-Image Export-06_c1_ORG.tif
Cells: 27
Processing: MEA_M12_3-Image Export-07_c1_ORG.tif
Cells: 11
Processing: MEA_M12_4-Image Export-08_c1_ORG.tif
Cells: 35
Processing: MEA_M13_1-Image Export-09_c1_ORG.tif
Cells: 3
Processing: MEA_M13_2-Image Export-10_c1_ORG.tif
Cells: 7
Processing: MEA_M13_3-Image Export-11_c1_ORG.tif
Cells: 2
Processing: MEA_M13_4-Image Export-12_c1_ORG.tif
Cells: 7
Processing: MEA_M14_1-Image Export-13_c1_ORG.tif
Cells: 15
Processing: MEA_M14_2-Image Export-14_c1_ORG.tif
Cells: 25
Processing: MEA_M14_3-Image Export-15_c1_ORG.tif
Cells: 22
Processing: MEA_M14_4-Image Export-16_c1_ORG.tif
Cells: 28
Processing: MEA_M15_1-Image Export-17_c1_ORG.tif
Cells: 62
Pro

FileNames Channel  Thresh  UseROI  AvgCellDiam  \
0   MEA_M10_1-Image Export-01_c1_ORG.tif     Ch1    36.0     1.0         10.0   
1   MEA_M10_2-Image Export-02_c1_ORG.tif     Ch1    36.0     1.0         10.0   
2   MEA_M10_3-Image Export-03_c1_ORG.tif     Ch1    36.0     1.0         10.0   
3   MEA_M10_4-Image Export-04_c1_ORG.tif     Ch1    36.0     1.0         10.0   
4   MEA_M12_1-Image Export-05_c1_ORG.tif     Ch1    36.0     1.0         10.0   
5   MEA_M12_2-Image Export-06_c1_ORG.tif     Ch1    36.0     1.0         10.0   
6   MEA_M12_3-Image Export-07_c1_ORG.tif     Ch1    36.0     1.0         10.0   
7   MEA_M12_4-Image Export-08_c1_ORG.tif     Ch1    36.0     1.0         10.0   
8   MEA_M13_1-Image Export-09_c1_ORG.tif     Ch1    36.0     1.0         10.0   
9   MEA_M13_2-Image Export-10_c1_ORG.tif     Ch1    36.0     1.0         10.0   
10  MEA_M13_3-Image Export-11_c1_ORG.tif     Ch1    36.0     1.0         10.0   
11  MEA_M13_4-Image Export-12_c1_ORG.tif     Ch1    36.0     1.0         10.0   
12  MEA_M14_1-Image Export-13_c1_ORG.tif     Ch1    36.0     1.0         10.0   
13  MEA_M14_2-Image Export-14_c1_ORG.tif     Ch1    36.0     1.0         10.0   
14  MEA_M14_3-Image Export-15_c1_ORG.tif     Ch1    36.0     1.0         10.0   
15  MEA_M14_4-Image Export-16_c1_ORG.tif     Ch1    36.0     1.0         10.0   
16  MEA_M15_1-Image Export-17_c1_ORG.tif     Ch1    36.0     1.0         10.0   
17  MEA_M15_2-Image Export-18_c1_ORG.tif     Ch1    36.0     1.0         10.0   
18  MEA_M15_3-Image Export-19_c1_ORG.tif     Ch1    36.0     1.0         10.0   
19  MEA_M15_4-Image Export-20_c1_ORG.tif     Ch1    36.0     1.0         10.0   
20  MEA_M16_1-Image Export-21_c1_ORG.tif     Ch1    36.0     1.0         10.0   
21  MEA_M16_2-Image Export-22_c1_ORG.tif     Ch1    36.0     1.0         10.0   
22  MEA_M16_3-Image Export-23_c1_ORG.tif     Ch1    36.0     1.0         10.0   
23  MEA_M16_4-Image Export-24_c1_ORG.tif     Ch1    36.0     1.0         10.0   
24  MEA_M18_1-Image Export-25_c1_ORG.tif     Ch1    36.0     1.0         10.0   
25  MEA_M18_2-Image Export-26_c1_ORG.tif     Ch1    36.0     1.0         10.0   
26  MEA_M18_3-Image Export-27_c1_ORG.tif     Ch1    36.0     1.0         10.0   
27  MEA_M18_4-Image Export-28_c1_ORG.tif     Ch1    36.0     1.0         10.0   
28  MEA_M19_1-Image Export-29_c1_ORG.tif     Ch1    36.0     1.0         10.0   
29  MEA_M19_2-Image Export-30_c1_ORG.tif     Ch1    36.0     1.0         10.0   
..                                   ...     ...     ...     ...          ...   
62  MEA_M28_3-Image Export-63_c1_ORG.tif     Ch1    36.0     1.0         10.0   
63  MEA_M28_4-Image Export-64_c1_ORG.tif     Ch1    36.0     1.0         10.0   
64  MEA_M29_1-Image Export-65_c1_ORG.tif     Ch1    36.0     1.0         10.0   
65  MEA_M29_2-Image Export-66_c1_ORG.tif     Ch1    36.0     1.0         10.0   
66  MEA_M29_3-Image Export-67_c1_ORG.tif     Ch1    36.0     1.0         10.0   
67  MEA_M29_4-Image Export-68_c1_ORG.tif     Ch1    36.0     1.0         10.0   
68  MEA_M31_1-Image Export-69_c1_ORG.tif     Ch1    36.0     1.0         10.0   
69  MEA_M31_2-Image Export-70_c1_ORG.tif     Ch1    36.0     1.0         10.0   
70  MEA_M31_3-Image Export-71_c1_ORG.tif     Ch1    36.0     1.0         10.0   
71  MEA_M31_4-Image Export-72_c1_ORG.tif     Ch1    36.0     1.0         10.0   
72  MEA_M35_1-Image Export-73_c1_ORG.tif     Ch1    36.0     1.0         10.0   
73  MEA_M35_2-Image Export-74_c1_ORG.tif     Ch1    36.0     1.0         10.0   
74  MEA_M35_3-Image Export-75_c1_ORG.tif     Ch1    36.0     1.0         10.0   
75  MEA_M35_4-Image Export-76_c1_ORG.tif     Ch1    36.0     1.0         10.0   
76  MEA_M36_1-Image Export-77_c1_ORG.tif     Ch1    36.0     1.0         10.0   
77  MEA_M36_2-Image Export-78_c1_ORG.tif     Ch1    36.0     1.0         10.0   
78  MEA_M36_3-Image Export-79_c1_ORG.tif     Ch1    36.0     1.0         10.0   
79  MEA_M36_4-Image Export-80_c1_ORG.tif     Ch1    36.0     1

# 6. Count Channel 2
Count all cells for channel 2 images and save to disk

In [ ]:
Ch2_Counts = cc.Count_folder(dirinfo,params,
                             Channel="Ch2",
                             UseROI=False,
                             UseWatershed=True)
Ch2_Counts.to_csv(os.path.join(os.path.normpath(dirinfo['output']), "Ch2_Counts.csv"))
Ch2_Counts

# 7. Count Overlapping Cells from Channels 1 and 2
Count cells overlapping in Channel 1 and Channel 2 and save results to disk
**Note:** Channels 1 and 2 must be counted before doing this
Count overlapping cells for channel 1 and channel 2

In [ ]:
Merge_Counts,Cells_Ch1 = cc.Merge_folder(dirinfo,params)
Merge_Counts.to_csv(os.path.join(os.path.normpath(dirinfo['output']), "Merge_Counts.csv"))
Merge_Counts